In [389]:
from urllib.request import Request, urlopen, quote
import urllib.error
import requests
from bs4 import BeautifulSoup as bs
import pandas as pd
from http.client import IncompleteRead
import time
from urllib.error import URLError

In [390]:
class Condo_khmer24:
    def __init__(self,pages):
        self.pages = pages
    def get_html(self, url, user_agent=False, timeout=10, max_retries=3,retry_delay=1):
        if user_agent:
            user_agent = user_agent
        else:
            user_agent = "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36"

        request = Request(url, headers={'User-Agent': user_agent})
        
        retries = 0

        while retries < max_retries:
            try:
                get_open = urlopen(request, timeout=timeout).read()
                return bs(get_open)
            except IncompleteRead as e:
                # Handle IncompleteRead exception
                print(f"IncompleteRead exception occurred: {e}")
                return None
            except URLError as e:
                # Handle URLError exception
                print(f"URLError occurred: {e}")
                retries += 1
                if retries >= max_retries:
                    print(f"Max retries exceeded. Unable to establish a connection to {url}")
                    return None
                time.sleep(retry_delay)

        return None

    def get_list_url_condo(self):
        links = []
        pages = self.pages
        for page in range(0, pages * 50, 50):
            url = f"https://www.khmer24.com/en/search.html?q=condo&category=&per_page={page}"
            html = self.get_html(url)
            if not html:
                continue
            list_item = html.find_all('li', class_="item")
            for i in range(len(list_item)):
                a_tag = list_item[i].a
                if a_tag:
                    url_link = quote(a_tag.get('href'), safe='/:')
                    request_link = self.get_html(url_link)
                    if not request_link:
                        continue
                    item_short_description = request_link.find('div', class_="item-short-description p-3 position-relative")
                    if item_short_description:
                        category_element = item_short_description.find('span', class_='title', text='Category :')
                        if category_element:
                            category = category_element.find_next_sibling('span').text.strip()
                            try:
                                if category == 'Condo for Sale':
                                    links.append(url_link)
                                else:
                                    continue
                            except:
                                pass
        return links
    def get_condo_data(self):
        description = {}
        link_condo_sales = self.get_list_url_condo()
        for link in link_condo_sales:
            try:
                html = self.get_html(link)
                item_short_description = html.find('div', class_="item-short-description p-3 position-relative")
                item_short_description2 = html.find('ul', class_="list-unstyled item-fields")
                item_details = html.find('div', class_="item-detail p-3")
                post_description_element = item_details.select_one('.post-description')
                post_description = post_description_element.get_text(separator='\n').strip() if post_description_element else None

                title_condo = item_short_description.h1.get_text()
                price = html.find('div', class_="item-short-description p-3 position-relative").div.p.get_text()

                if item_short_description and item_short_description2:
                    title_condo = item_short_description.h1.get_text()
                    price = html.find('div', class_="item-short-description p-3 position-relative").div.p.get_text()

                    list_description = item_short_description.find_all('li')
                    if item_short_description2:
                        list_description += item_short_description2.find_all('li')

                title_list = []
                value_list = []
                for i in range(len(list_description)):
                    title = list_description[i].find('span', class_='title').get_text()
                    value = list_description[i].find('span', class_='value').get_text()

                    if ':' in title:
                        title = title.replace(':', '')

                    title_list.append(title)
                    value_list.append(value)

                    if not description or title not in description:
                        description[title] = [value]
                    else:
                        description[title].append(value)

                keys = description.keys()

                key_list = ['Size(m2)', 'Bedroom', 'Bathroom', 'Link', 'Title', 'Price', 'Post Description']
                for key in key_list:
                    if key not in list(keys):
                        description[key] = []
                

                for key in keys:
                    if key not in title_list + ['Link', 'Title', 'Price', 'Post Description']:
                        description[key].append('NaN')

                values = [link, title_condo, price, post_description]

                for i, title in enumerate(['Link', 'Title', 'Price', 'Post Description']):
                    if not description or title not in description:
                        description[title] = [values[i]]
                    else:
                        description[title].append(values[i])
            except urllib.error.URLError as e:
                print(f"Error occurred while accessing URL: {link}")
                print(f"Error message: {e}")
                continue  # Move to the next link
        return description

In [391]:
scrap = Condo_khmer24(83)


In [392]:
data = scrap.get_condo_data()
data

URLError occurred: <urlopen error [WinError 10054] An existing connection was forcibly closed by the remote host>


{'Ad ID ': ['8538993',
  '8517524',
  '9617339',
  '9617339',
  '8134344',
  '8488161',
  '8547359',
  '8601253',
  '8604997',
  '8611905',
  '8728735',
  '8728751',
  '8728765',
  '8778924',
  '8894227',
  '9062934',
  '9091033',
  '9111383',
  '9468201',
  '9540211',
  '9574282',
  '9574282',
  '9574282',
  '7824509',
  '7826362',
  '8499759',
  '8526816',
  '8553585',
  '8553585',
  '8607972',
  '8729386',
  '8829137',
  '8837997',
  '8908815',
  '8958365',
  '9008430',
  '9008532',
  '9044643',
  '9086306',
  '9107438',
  '9130611',
  '9142059',
  '9163679',
  '9238703',
  '9363369',
  '9363369',
  '9363369',
  '9559572',
  '9559572',
  '9541475',
  '9500716',
  '9619917',
  '9619917',
  '9619917',
  '9619917',
  '9656448',
  '9330721',
  '8523185',
  '7791074',
  '7826214',
  '7899341',
  '7954808',
  '8095311',
  '8116812',
  '8116812',
  '8156142',
  '8163550',
  '8215749',
  '8237721',
  '8302638',
  '8345621',
  '8370559',
  '8469381',
  '8501823',
  '8510041',
  '8526331',
  

In [394]:
data.keys()

dict_keys(['Ad ID ', 'Category ', 'Locations ', 'Posted ', 'Size(m2)', 'Bedroom', 'Bathroom', 'Link', 'Title', 'Price', 'Post Description'])

In [387]:
import pandas as pd

In [395]:
df = pd.DataFrame(data)
df

Ad ID        Category   Locations     Posted  Size(m2) Bedroom  \
0     8538993  Condo for Sale  Phnom Penh  06-Jul-23       34     NaN   
1     8517524  Condo for Sale  Phnom Penh  06-Jul-23       58     NaN   
2     9617339  Condo for Sale  Phnom Penh  03-Jul-23       34     NaN   
3     9617339  Condo for Sale  Phnom Penh  03-Jul-23       34     NaN   
4     8134344  Condo for Sale  Phnom Penh  09-Apr-23       57     NaN   
...       ...             ...         ...        ...      ...     ...   
1542  9669962  Condo for Sale  Phnom Penh  07-Jul-23       57     NaN   
1543  9670149  Condo for Sale  Phnom Penh  08-Jul-23   298616     NaN   
1544  9665839  Condo for Sale  Phnom Penh  07-Jul-23      119     NaN   
1545  8528328  Condo for Sale  Phnom Penh  07-Jul-23       32     NaN   
1546  8750427  Condo for Sale  Phnom Penh  07-Jul-23       32     NaN   

     Bathroom                                               Link  \
0         NaN  https://www.khmer24.com/en/property/new-condo-...   
1         NaN  https://www.khmer24.com/en/property/vista-cond...   
2         NaN  https://www.khmer24.com/en/property/condo-uk-5...   
3         NaN  https://www.khmer24.com/en/property/condo-%E1%...   
4         NaN  https://www.khmer24.com/en/property/condo-for-...   
...       ...                                                ...   
1542      NaN  https://www.khmer24.com/en/property/ud83cudfe0...   
1543      NaN  https://www.khmer24.com/en/property/condo-sale...   
1544      NaN  https://www.khmer24.com/en/property/beautifull...   
1545      NaN  https://www.khmer24.com/en/property/%E1%9E%81%...   
1546      NaN  https://www.khmer24.com/en/property/chip-mong-...   

                                                  Title     Price  \
0                                    New condo for sell   $58,000   
1                              Vista Condo Aeon2 Urgent   $75,000   
2                                Condo UK 548 for Sales   $42,000   
3     Condo សម្រាប់ជួល/Condo for Rent (The Peak Priv...      $800   
4                                   Condo for sale 57m2   $72,000   
...                                                 ...       ...   
1542  🏠ខុនដូ Agile Sky Residence (ជាន់ទី31) សម្រាប់ជ...      $900   
1543                     Condo sale 2Bedroom លក់បន្ទាន់   $17,900   
1544  --- BEAUTIFULL WHOLE CORNER Three Bedrooms at ...  $350,000   
1545  ខុនដូ 1 បន្ទប់គេង ត្រូវការលក់បន្ទាន់ Park Land...   $10,000   
1546                           Chip Mong Parkland Condo   $59,500   

                                       Post Description  
0     Very special promotion!! Full price $58,000 bu...  
1     ខុនដូសម្រាប់លក់ VISTA Condo\n\r\n(English Belo...  
2     បន្ទប់ខុនដូប្រភេទ Studio (UK Condo 548)\n\rកណ្...  
3     Property Code: VBRE00586\n\r\nCondo សម្រាប់ជួល...  
4     Fully furnished condo for sale / rent \n\nOwne...  
...                                                 ...  
1542  (English Below)\n\r\n🏠ខុនដូ Agile Sky Residenc...  
1543  ខុ​នដូទំនេីក្នុងគម្រោងMorgan Enmainson \n\nប្រ...  
1544  --- BEAUTIFULL WHOLE CORNER Three Bedrooms at ...  
1545  អ្នកលក់ម្ចាស់ផ្ទាល់ និងអាចចូលស្នាក់នៅខែតុលានេះ...  
1546  -Contingency Service Per Month：44.8$ including...  

[1547 rows x 11 columns]

In [398]:
df.to_csv('Condo782023.csv', index= False)

In [143]:
import pandas as pd
df = pd.read_csv("Condo782023.csv")

In [144]:
df.isnull().sum()

Ad ID                  0
Category               0
Locations              0
Posted                 0
Size(m2)               0
Bedroom             1547
Bathroom            1547
Link                   0
Title                  0
Price                  0
Post Description       0
dtype: int64

In [145]:
df.columns

Index(['Ad ID ', 'Category ', 'Locations ', 'Posted ', 'Size(m2)', 'Bedroom',
       'Bathroom', 'Link', 'Title', 'Price', 'Post Description'],
      dtype='object')

In [146]:
df['Locations '].value_counts()

Phnom Penh        1452
Preah Sihanouk      47
Siem Reap           30
Kandal              17
Takeo                1
Name: Locations , dtype: int64

In [147]:
row_takoe =df[df['Locations ']=='Takeo']
row_takoe

Ad ID        Category  Locations     Posted   Size(m2)  Bedroom  \
75  8526331  Condo for Sale      Takeo  07-Jul-23       100      NaN   

    Bathroom                                               Link  \
75       NaN  https://www.khmer24.com/en/property/condo-for-...   

                                           Title     Price  \
75  Condo for sale (The Bridge) $225,000(100m2)   $225,000   

                                     Post Description  
75  Condo for sale (The Bridge) $225,000(100m2) \n...

In [148]:
row_Preah_Sihanouk =df[df['Locations ']=='Preah Sihanouk']
row_Siem_Reap =df[df['Locations ']=='Siem Reap']
row_Kandal =df[df['Locations ']=='Kandal']

In [149]:
row_takoe.to_csv('row_takoe.csv', index=False)

In [150]:
row_Preah_Sihanouk.to_csv('row_Preah_Sihanouk.csv',index=False)
row_Siem_Reap.to_csv('row_Siem_Reap.csv', index=False)
row_Kandal.to_csv('row_Kandal.csv',index=False)

In [151]:
df['Post Description'].count()

1547

In [152]:
df['Post Description'].unique()

array(['Very special promotion!! Full price $58,000 but you pay owner $35,000,  and $23,000you can pay with company. It has 1 bedroom Royal Park Condo new condo in Phnom Penh\n\r\nFloor 6 in front of street 608\n\n\n\n\n\r\nmanagement fee $0.9/m2 (around $20 per month)\n\n\n\r\nLocation: Toul Kork and it closes to Toul Kork roundabout  and behind Institute of Foreign Language (IFL) street 608….etc\n\n\n\n\n\r\nFully furnished\n\r\n1 bedroom\n\r\n1 bathroom\n\r\n1 Living room\n\r\n1 Kitchen\n\r\n1 Hot water\n\r\nSize: 34.76 sqm\n\n\n\n\n\r\n Motor parking free, Elevator, Gym, Swimming pool, and sky bar.\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\r\nFeel free to call or email me (Personal condo) for more information via: \n098266xxx \nចុចដើម្បីតេ/Click To Call\n/ \n017266xxx \nចុចដើម្បីតេ/Click To Call\n (Telegram)\n\n\n\r\n* ខុនដូ នៅខាងក្រោយវិទ្យាស្ថានភាសាបរទេស បែបទំនើប និងទាន់សម័យ Royal Park Condo ត្រូវការលក់បន្ទន់ពីម្ចាស់ផ្ទាល់តម្លៃពេញ $58,000 ការបង់ប្រាក់ជាមួយម្ចាស់មានភាពងាយស្រួល និងបត់បែន មា

-----------

In [153]:
description = df['Post Description']

In [154]:
df_description = pd.DataFrame(description)

In [155]:
df_title_description=df[['Title','Post Description']]

In [156]:
df_title_description.to_csv("title_description_condo.csv", index=False)

In [157]:
df_description.to_csv("Description Condo for sale.csv", index=False)

In [158]:
import re
def extract_location(description):
    if isinstance(description, str):
        # Search for "Toul Kork" in the description
        match = re.search(r'Toul\s+Kork', description, re.IGNORECASE)
        if match:
            return match.group(0).title()
        # Search for "Toul Kork" in the description
        match = re.search(r'Toul\s+Kork|ទួល\s*គោក|Boeng\s+Kak\s+1|Boeng\s+Kak\s+2|Boeng\s+Salang|Phsar\s+Daeum\s+Kor|Phsar\s+Depou\s+1|Phsar\s+Depou\s+2|Phsar\s+Depou\s+3|Tuek\s+L\'ak\s+1|Tuek\s+L\'ak\s+2|Tuek\s+L\'ak\s+3|ទឹកល្អក់ទី\s+១|ទឹកល្អក់ទី\s+២|ទឹកល្អក់ទី\s+៣|បឹងកក់ទី\s+១|បឹងកក់ទី\s+២|បឹងកក់ទី\s+៣|បឹងសាឡាង|ផ្សារដើមគរ|ផ្សារដេប៉ូទី\s+១|ផ្សារដេប៉ូទី\s+២|ផ្សារដេប៉ូទី\s+៣', description, re.IGNORECASE)
        if match:
            translate = {'ទួលគោក':'Toul Kork',
                        'Boeng Kak 1': 'Toul Kork', 'Boeng Kak 2': 'Toul Kork',
                         'Boeng Salang': 'Toul Kork',
                         'Phsar Daeum Kor': 'Toul Kork',
                         'Phsar Depou 1': 'Toul Kork', 
                         'Phsar Depou 2': 'Toul Kork', 'Phsar Depou 3': 'Toul Kork',
                         'Tuek L\'ak 1': 'Toul Kork', 'Tuek L\'ak 2': 'Toul Kork',
                         'Tuek L\'ak 3': 'Toul Kork', 'ទឹកល្អក់ទី ១': 'Toul Kork',
                         'ទឹកល្អក់ទី ២': 'Toul Kork', 'ទឹកល្អក់ទី ៣': 'Toul Kork',
                         'បឹងកក់ទី ១': 'Toul Kork', 'បឹងកក់ទី ២': 'Toul Kork',
                         'បឹងកក់ទី ៣': 'Toul Kork', 'បឹងសាឡាង': 'Toul Kork',
                         'ផ្សារដើមគរ': 'Toul Kork',
                         'ផ្សារដេប៉ូទី ១': 'Toul Kork',
                         'ផ្សារដេប៉ូទី ២': 'Toul Kork',
                         'ផ្សារដេប៉ូទី ៣': 'Toul Kork'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())

        
        match = re.search(r'Chamkar\s+Mon', description, re.IGNORECASE)
        if match:
            return match.group(0).title()
        match = re.search(r'Chamkar\s+Mon|ចំការ\s*មន', description, re.IGNORECASE)
        if match:
            translate = {'ចំការមន':'Chamkar Mon'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
#         match = re.search(r'Daun\s+Penh', description, re.IGNORECASE)
#         if match:
#             return match.group(0).title()
        match = re.search(r'Daun\s+Penh|ដូន\s*ពេញ|Doun\s+Penh|Boeng\s+Rang|Chakto\s+Mukh|Chey\s+Chumneah|Phsar\s+Chas|Phsar\s+Kandal\s+1|Phsar\s+Kandal\s+2|Phsar\s+Thei\s+1|Phsar\s+Thei\s+2|Phsar\s+Thei\s+3|Srah\s+Chak|Voat\s+Phnum|ដូន\s+ពេញ|ចតុមុខ|ជ័យជំនះ|បឹងរាំង|ផ្សារកណ្ដាល\s+១|ផ្សារកណ្ដាល\s+២|ផ្សារចាស់|ផ្សារថ្មីទី\s+១|ផ្សារថ្មីទី\s+២|ផ្សារថ្មីទី\s+៣|វត្តភ្នំ|ស្រះចក', description, re.IGNORECASE)
        if match:
            translate = {'ដូនពេញ':'Daun Penh','Doun Penh': 'Daun Penh', 'Boeng Rang': 'Daun Penh', 'Chakto Mukh': 'Daun Penh', 'Chey Chumneah': 'Daun Penh', 'Phsar Chas': 'Daun Penh', 'Phsar Kandal 1': 'Daun Penh', 'Phsar Kandal 2': 'Daun Penh', 'Phsar Thei 1': 'Daun Penh', 'Phsar Thei 2': 'Daun Penh', 'Phsar Thei 3': 'Daun Penh', 'Srah Chak': 'Daun Penh', 'Voat Phnum': 'Daun Penh', 'ដូនពេញ': 'Daun Penh', 'ចតុមុខ': 'Daun Penh', 'ជ័យជំនះ': 'Daun Penh', 'បឹងរាំង': 'Daun Penh', 'ផ្សារកណ្ដាល ១': 'Daun Penh', 'ផ្សារកណ្ដាល ២': 'Daun Penh', 'ផ្សារចាស់': 'Daun Penh', 'ផ្សារថ្មីទី ១': 'Daun Penh', 'ផ្សារថ្មីទី ២': 'Daun Penh', 'ផ្សារថ្មីទី ៣': 'Daun Penh', 'វត្តភ្នំ': 'Daun Penh', 'ស្រះចក': 'Daun Penh'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Prampir\s+Makara|៧\s*មករា|ប្រាំពីរ\s*មករា|ប្រាំពី\s*មករា|7\s*មករា|Boeng\s+Proluet|Mittapheap|Monourrom|Ou\s+Ruessei\s+1|Ou\s+Ruessei\s+2|Ou\s+Ruessei\s+3|Ou\s+Ruessei\s+4|Veal\s+Vong|បឹង\s+ព្រលិត|មនោ\s+រម្យ|មិត្ត\s+ភាព|វាល\s+វង់|អូរឬស្សីទី\s+១|អូរឬស្សីទី\s+២|អូរឬស្សីទី\s+៣|អូរឬស្សីទី\s+៤', description, re.IGNORECASE)
        if match:
            translate = {'៧មករា':'Prampir Makara',
                         'ប្រាំពីរមករា':'Prampir Makara',
                         'ប្រាំពីមករា':'Prampir Makara',
                         '7មករា':'Prampir Makara',
                         '7 មករា':'Prampir Makara',
                        'Boeng Proluet': 'Prampir Makara',
                        'Mittapheap': 'Prampir Makara',
                        'Monourrom': 'Prampir Makara',
                        'Ou Ruessei1': 'Prampir Makara',
                        'Ou Ruessei2': 'Prampir Makara',
                        'Ou Ruessei3': 'Prampir Makara',
                        'Ou Ruessei4': 'Prampir Makara',
                        'Veal Vong': 'Prampir Makara',
                        'បឹងព្រលិត': 'Prampir Makara',
                        'មនោរម្យ': 'Prampir Makara',
                        'មិត្តភាព': 'Prampir Makara',
                        'វាលវង់': 'Prampir Makara',
                        'អូរឬស្សីទី១': 'Prampir Makara',
                        'អូរឬស្សីទី​២': 'Prampir Makara',
                        'អូរឬស្សីទី៣': 'Prampir Makara',
                        'អូរឬស្សីទី៤': 'Prampir Makara'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Pur\s+Senchey|ពោធិ៍សែនជ័យ|កន្ទោក|កាកាបទី\s+១|កាកាបទី\s+២|កំបូល|ចោមចៅទី\s+១|ចោមចៅទី\s+២|ចោមចៅទី\s+៣|ត្រពាំងក្រសាំង|បឹងធំ|ភ្លើងឆេះរទេះ|សំរោងក្រោម|ស្នោរ|ឳឡោក|Boeng\s+Thum|Chaom\s+Chau\s+1|Chaom\s+Chau\s+2|Chaom\s+Chau\s+3|Kakab\s+1|Kakab\s+2|Kamboul|Kantaok|Ovlaok|Phleung\s+Chheh\s+Roteh|Samraong\s+Kraom|Snaor|Trapeang\s+Krasang', description, re.IGNORECASE)
        if match:
            translate = {'ពោធិ៍សែនជ័យ': 'Pur Senchey', 'កន្ទោក': 'Pur Senchey', 'កាកាបទី ១': 'Pur Senchey', 'កាកាបទី ២': 'Pur Senchey', 'កំបូល': 'Pur Senchey', 'ចោមចៅទី ១': 'Pur Senchey', 'ចោមចៅទី ២': 'Pur Senchey', 'ចោមចៅទី ៣': 'Pur Senchey', 'ត្រពាំងក្រសាំង': 'Pur Senchey', 'បឹងធំ': 'Pur Senchey', 'ភ្លើងឆេះរទេះ': 'Pur Senchey', 'សំរោងក្រោម': 'Pur Senchey', 'ស្នោរ': 'Pur Senchey', 'ឳឡោក': 'Pur Senchey', 'Boeng Thum': 'Pur Senchey', 'Chaom Chau 1': 'Pur Senchey', 'Chaom Chau 2': 'Pur Senchey', 'Chaom Chau 3': 'Pur Senchey', 'Kakab 1': 'Pur Senchey', 'Kakab 2': 'Pur Senchey', 'Kamboul': 'Pur Senchey', 'Kantaok': 'Pur Senchey', 'Ovlaok': 'Pur Senchey', 'Phleung Chheh Roteh': 'Pur Senchey', 'Samraong Kraom': 'Pur Senchey', 'Snaor': 'Pur Senchey', 'Trapeang Krasang': 'Pur Senchey'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'AEON|Sen\s+Sok|Khmuonh|Kouk\s+Khleang|Krang\s+Thnong|Ou\s+Baek\s+K\'am|Phnom\s+Penh\s+Thmei|Tuek\s+Thla|ខណ្ឌ\s+សែនសុខ|ក្រាំងធ្នង់|គោកឃ្លាង|ឃ្មួញ|ទឹកថ្លា|ភ្នំពេញថ្មី|អូរបែកក្អម', description, re.IGNORECASE)
        if match:
            translate = { 'Aeon                 ':'Sen Sok','Aeon   ':'Sen Sok','Aeon': 'Sen Sok','AEON': 'Sen Sok','Khmuonh': 'Sen Sok', 'Kouk Khleang': 'Sen Sok', 'Krang Thnong': 'Sen Sok', 'Ou Baek K\'am': 'Sen Sok', 'Phnom Penh Thmei': 'Sen Sok', 'Tuek Thla': 'Sen Sok', 'ខណ្ឌ សែនសុខ': 'Sen Sok', 'ក្រាំងធ្នង់': 'Sen Sok', 'គោកឃ្លាង': 'Sen Sok', 'ឃ្មួញ': 'Sen Sok', 'ទឹកថ្លា': 'Sen Sok', 'ភ្នំពេញថ្មី': 'Sen Sok', 'អូរបែកក្អម': 'Sen Sok'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Chbar\s+Ampov|Chbar\s+Ampov\s+1|Chbar\s+Ampov\s+2|Kbal\s+Kaoh|Nirouth|Preaek\s+Aeng|Preaek\s+Pra|Preaek\s+Thmei|Veal\s+Sbov|ច្បារអំពៅ|ក្បាលកោះ|ច្បារអំពៅទី\s+១|ច្បារអំពៅទី\s+២|និរោធ|ព្រែកថ្មី|ព្រែកប្រា|ព្រែកឯង|វាលស្បូវ', description, re.IGNORECASE)
        if match:
            translate = {'Chbar Ampov': 'Chbar Ampov', 'Chbar Ampov 1': 'Chbar Ampov', 'Chbar Ampov 2': 'Chbar Ampov', 'Kbal Kaoh': 'Chbar Ampov', 'Nirouth': 'Chbar Ampov', 'Preaek Aeng': 'Chbar Ampov', 'Preaek Pra': 'Chbar Ampov', 'Preaek Thmei': 'Chbar Ampov', 'Veal Sbov': 'Chbar Ampov', 'ច្បារអំពៅ': 'Chbar Ampov', 'ក្បាលកោះ': 'Chbar Ampov', 'ច្បារអំពៅទី ១': 'Chbar Ampov', 'ច្បារអំពៅទី ២': 'Chbar Ampov', 'និរោធ': 'Chbar Ampov', 'ព្រែកថ្មី': 'Chbar Ampov', 'ព្រែកប្រា': 'Chbar Ampov', 'ព្រែកឯង': 'Chbar Ampov', 'វាលស្បូវ': 'Chbar Ampov'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Dangkao|Pong\s+Tuek|Prey\s+Veaeng|Prey\s+Sa|Krang\s+Pongro|Prateah\s+Lang|Sak\s+Sampov|Cheung\s+Aek|Kong\s+Noy|Preaek\s+Kampues|Roluos|Spean\s+Thma|Tien|ពុងទឹក|ព្រៃវែង|ព្រៃសា|ក្រាំងពង្រ|ប្រេតឡាង|សាក់សំពៅ|ជើងឯក|គង់\s+ណយ|ព្រែកកំពឹស|រលួស|ស្ពានថ្ម|ទៀន', description, re.IGNORECASE)
        if match:
            translate = {'ពុងទឹក': 'Dangkao', 'ព្រៃវែង': 'Dangkao', 'ព្រៃសា': 'Dangkao', 'ក្រាំងពង្រ': 'Dangkao', 'ប្រេតឡាង': 'Dangkao', 'សាក់សំពៅ': 'Dangkao', 'ជើងឯក': 'Dangkao', 'គង់ ណយ': 'Dangkao', 'ព្រែកកំពឹស': 'Dangkao', 'រលួស': 'Dangkao', 'ស្ពានថ្ម': 'Dangkao', 'ទៀន': 'Dangkao', 'Pong Tuek': 'Dangkao', 'Prey Veaeng': 'Dangkao', 'Prey Sa': 'Dangkao', 'Krang Pongro': 'Dangkao', 'Prateah Lang': 'Dangkao', 'Sak Sampov': 'Dangkao', 'Cheung Aek': 'Dangkao', 'Kong Noy': 'Dangkao', 'Preaek Kampues': 'Dangkao', 'Roluos': 'Dangkao', 'Spean Thma': 'Dangkao', 'Tien': 'Dangkao'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())

# Loop through all elements and extract the locations
        match = re.search(r'Mean\s+Chey|មានជ័យ|Chak\s+Angrae\s+Leu|Chak\s+Angrae\s+Kraom|Stueng\s+Mean\s+Chey\s+1|Stueng\s+Mean\s+Chey\s+2|Stueng\s+Mean\s+Chey\s+3|Boeng\s+Tumpun\s+1|Boeng\s+Tumpun\s+2', description, re.IGNORECASE)
        if match:
            translate = {'មានជ័យ': 'Mean Chey', 'Chak Angrae Leu': 'Mean Chey', 'Chak Angrae Kraom': 'Mean Chey', 'Stueng Mean Chey 1': 'Mean Chey', 'Stueng Mean Chey 2': 'Mean Chey', 'Stueng Mean Chey 3': 'Mean Chey', 'Boeng Tumpun 1': 'Mean Chey', 'Boeng Tumpun 2': 'Mean Chey'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Russey\s+Keo|Chrang\s+Chamreh\s+1|Chrang\s+Chamreh\s+2|Kilomet\s+Lekh\s+Prammouy|Ruessei\s+Kaev|Svay\s+Pak|Tuol\s+Sangkae\s+1|Tuol\s+Sangkae\s+2|ឬស្សីកែវ|គីឡូម៉ែតលេខ៦|ច្រាំងចំរេះទី\s+១|ច្រាំងចំរេះទី\s+២|ទួលសង្កែទី\s+១|ទួលសង្កែទី\s+២|ស្វាយប៉ាក|ឬស្សីកែវ', description, re.IGNORECASE)
        if match:
            translate = {'Chrang Chamreh 1': 'Russey Keo', 'Chrang Chamreh 2': 'Russey Keo', 'Kilomet Lekh Prammouy': 'Russey Keo', 'Ruessei Kaev': 'Russey Keo', 'Svay Pak': 'Russey Keo', 'Tuol Sangkae 1': 'Russey Keo', 'Tuol Sangkae 2': 'Russey Keo', 'ឬស្សីកែវ': 'Russey Keo', 'គីឡូម៉ែតលេខ៦': 'Russey Keo', 'ច្រាំងចំរេះទី ១': 'Russey Keo', 'ច្រាំងចំរេះទី ២': 'Russey Keo', 'ទួលសង្កែទី ១': 'Russey Keo', 'ទួលសង្កែទី ២': 'Russey Keo', 'ស្វាយប៉ាក': 'Russey Keo'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Boeung\s+Keng\s+Kang\s+I|Boeung\s+Keng\s+Kang\s+1|Boeung\s+Keng\s+Kang|Boeng\s+Keng\s+Kang|Boeung\s+Keng\s+Kang\s+I|Boeng\s+Keng\s+Kang\s+II|Boeng\s+Keng\s+Kang\s+III|Olampik|Tumnob\s+Tuek|Tuol\s+Svay\s+Prey\s+I|Tuol\s+Svay\s+Prey\s+II|បឹងកេងកងទី១|បឹងកេងកងទី២|បឹងកេងកងទី៣|អូឡាំពិក|ទំនប់ទឹក|ទួលស្វាយព្រៃទី១|ទួលស្វាយព្រៃទី២', description, re.IGNORECASE)
        if match:
            translate = { 'Boeung Keng Kang': 'Boeng Keng Kang','Boeung Keng Kang ': 'Boeng Keng Kang','Boeung Keng Kang I': 'Boeng Keng Kang','Boeung Keng Kang 1': 'Boeng Keng Kang', 'Boeng Keng Kang II': 'Boeng Keng Kang', 'Boeng Keng Kang III': 'Boeng Keng Kang', 'Olampik': 'Boeng Keng Kang', 'Tumnob Tuek': 'Boeng Keng Kang', 'Tuol Svay Prey I': 'Boeng Keng Kang', 'Tuol Svay Prey II': 'Boeng Keng Kang', 'បឹងកេងកងទី១': 'Boeng Keng Kang', 'បឹងកេងកងទី២': 'Boeng Keng Kang', 'បឹងកេងកងទី៣': 'Boeng Keng Kang', 'អូឡាំពិក': 'Boeng Keng Kang', 'ទំនប់ទឹក': 'Boeng Keng Kang', 'ទួលស្វាយព្រៃទី១': 'Boeng Keng Kang', 'ទួលស្វាយព្រៃទី២': 'Boeng Keng Kang'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Chroy\s+Changvar|Prek\s+Leap|Prek\s+Ta\s+Sek|Chroy\s+Changvar|Bak\s+Khaeng|Koh\s+Dach|ព្រែកលាប|ព្រែកតាសេក|ជ្រោយចង្វារ|បាក់ខែង|កោះដាច់', description, re.IGNORECASE)
        if match:
            translate = {'Prek Leap': 'Chroy Changvar', 'Prek Ta Sek': 'Chroy Changvar', 'Bak Khaeng': 'Chroy Changvar', 'Koh Dach': 'Chroy Changvar', 'ព្រែកលាប': 'Chroy Changvar', 'ព្រែកតាសេក': 'Chroy Changvar', 'ជ្រោយចង្វារ': 'Chroy Changvar', 'បាក់ខែង': 'Chroy Changvar', 'កោះដាច់': 'Chroy Changvar'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Prek\s+Pnov|Ponhea\s+Pon|Prek\s+Pnov|Samraong|Kouk\s+Roka|Ponsang|ពញាពន់|ព្រែកព្នៅ|សំរោង|គោករកា|ពនសាំង', description, re.IGNORECASE)
        if match:
            translate = {'Prek Pnov': 'Prek Pnov', 'Ponhea Pon': 'Prek Pnov', 'Prek Pnov': 'Prek Pnov', 'Samraong': 'Prek Pnov', 'Kouk Roka': 'Prek Pnov', 'Ponsang': 'Prek Pnov', 'ពញាពន់': 'Prek Pnov', 'ព្រែកព្នៅ': 'Prek Pnov', 'សំរោង': 'Prek Pnov', 'គោករកា': 'Prek Pnov', 'ពនសាំង': 'Prek Pnov'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Kamboul|Kantouk|Ovlaok|Snaor|Phleung\s+Chheh\s+Roteh|Boeng\s+Thum|Prateah\s+Lang|កំបូល|កន្ទោក|ឪឡោក|ស្នោរ|ភ្លើងឆេះរទេះ|បឹងធំ|ប្រទះឡាង', description, re.IGNORECASE | re.UNICODE)
        if match:
            translate = {'Kamboul': 'Kamboul', 'Kantouk': 'Kamboul', 'Ovlaok': 'Kamboul', 'Snaor': 'Kamboul', 'Phleung Chheh Roteh': 'Kamboul', 'Boeng Thum': 'Kamboul', 'Prateah Lang': 'Kamboul', 'កំបូល': 'Kamboul', 'កន្ទោក': 'Kamboul', 'ឪឡោក': 'Kamboul', 'ស្នោរ': 'Kamboul', 'ភ្លើងឆេះរទេះ': 'Kamboul', 'បឹងធំ': 'Kamboul', 'ប្រទះឡាង': 'Kamboul'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Thmei|Barku|Sambuor|Ta\s+Lei|Khva', description, re.IGNORECASE)
        if match:
            translate = {'Thmei': 'Dangkao', 'Barku': 'Dangkao', 'Sambuor': 'Dangkao', 'Ta Lei': 'Dangkao', 'Khva': 'Dangkao'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Kampong\s+Som|កំពង់សោម|ព្រៃនប់|ស្រុកស្ទឹងហាវ|ស្រុកកំពង់សីលា|កោះរ៉ុង|ក្រុងព្រះសីហនុ|សង្កាត់មួយ|សង្កាត់ពីរ|សង្កាត់បី|សង្កាត់បួន|Prey\s+Nob|Stueng\s+Hav|Kampong\s+Seila|Koh\s+Rong|Sangkat\s+Muoy|Sangkat\s+Pir|Sangkat\s+Bei|Sangkat\s+Buon', description, re.IGNORECASE)
        if match:
            translate = {'កំពង់សោម': 'Kampong Som', 'ព្រៃនប់': 'Kampong Som', 'ស្រុកស្ទឹងហាវ': 'Kampong Som', 'ស្រុកកំពង់សីលា': 'Kampong Som', 'កោះរ៉ុង': 'Kampong Som', 'ក្រុងព្រះសីហនុ': 'Kampong Som', 'សង្កាត់មួយ': 'Kampong Som', 'សង្កាត់ពីរ': 'Kampong Som', 'សង្កាត់បី': 'Kampong Som', 'សង្កាត់បួន': 'Kampong Som', 'Prey Nob': 'Kampong Som', 'Stueng Hav': 'Kampong Som', 'Kampong Seila': 'Kampong Som', 'Koh Rong': 'Kampong Som', 'Sangkat Muoy': 'Kampong Som', 'Sangkat Pir': 'Kampong Som', 'Sangkat Bei': 'Kampong Som', 'Sangkat Buon': 'Kampong Som'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Kandal|Kandal\s+Steung|Kien\s+Svay|Khsach\s+Kandal|Kaoh\s+Thum|Leuk\s+Daek|Lvea\s+Aem|Mukh\s+Kampul|Angk\s+Snuol|Ponhea\s+Leur|S\'ang|Ta\s+Khmau|ខេត្តកណ្ដាល|តាខ្មៅ|ស្អាង|ពញាឮ|អង្គស្នួល|មុខកំពូល|ល្វាឯម|លើកដែក|កោះធំ|ខ្សាច់កណ្តាល|កៀនស្វាយ|កណ្តាលស្ទឹង', description, re.IGNORECASE)
        if match:
            translate = {'Kandal': 'Lvea Aem', 'Kandal Steung': 'Lvea Aem', 'Kien Svay': 'Lvea Aem', 'Khsach Kandal': 'Lvea Aem', 'Kaoh Thum': 'Lvea Aem', 'Leuk Daek': 'Lvea Aem', 'Lvea Aem': 'Lvea Aem', 'Mukh Kampul': 'Lvea Aem', 'Angk Snuol': 'Lvea Aem', 'Ponhea Leur': 'Lvea Aem', 'S\'ang': 'Lvea Aem', 'Ta Khmau': 'Lvea Aem', 'ខេត្តកណ្ដាល': 'Lvea Aem', 'តាខ្មៅ': 'Lvea Aem', 'ស្អាង': 'Lvea Aem', 'ពញាឮ': 'Lvea Aem', 'អង្គស្នួល': 'Lvea Aem', 'មុខកំពូល': 'Lvea Aem', 'ល្វាឯម': 'Lvea Aem', 'លើកដែក': 'Lvea Aem', 'កោះធំ': 'Lvea Aem', 'ខ្សាច់កណ្តាល': 'Lvea Aem', 'កៀនស្វាយ': 'Lvea Aem', 'កណ្តាលស្ទឹង': 'Lvea Aem'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())
        match = re.search(r'Siem\s+Reap|Angkor\s+wat|Angkor\s+Chum|Angkor\s+Thom|Banteay\s+Srei|Chi\s+Kraeng|Kralanh|Puok|Prasat\s+Bakong|Siem\s+Reap\s+municipality|Sout\s+Nikom|Srei\s+Snam|Svay\s+Leu|Varin|អង្គរជុំ|អង្គរធំ|បន្ទាយស្រី|ជីក្រែង|ក្រលាញ់|ពួក|ប្រាសាទបាគង|សៀមរាប|សូទ្រនិគម|ស្រីស្នំ|ស្វាយលើ|វ៉ារិន', description, re.IGNORECASE)
        if match:
            translate = {'Siem Reap': 'Near Angkor Wat', 'Angkor wat': 'Near Angkor Wat', 'Angkor Chum': 'Near Angkor Wat', 'Angkor Thom': 'Near Angkor Wat', 'Banteay Srei': 'Near Angkor Wat', 'Chi Kraeng': 'Near Angkor Wat', 'Kralanh': 'Near Angkor Wat', 'Puok': 'Near Angkor Wat', 'Prasat Bakong': 'Near Angkor Wat', 'Siem Reap municipality': 'Near Angkor Wat', 'Sout Nikom': 'Near Angkor Wat', 'Srei Snam': 'Near Angkor Wat', 'Svay Leu': 'Near Angkor Wat', 'Varin': 'Near Angkor Wat', 'អង្គរជុំ': 'Near Angkor Wat', 'អង្គរធំ': 'Near Angkor Wat', 'បន្ទាយស្រី': 'Near Angkor Wat', 'ជីក្រែង': 'Near Angkor Wat', 'ក្រលាញ់': 'Near Angkor Wat', 'ពួក': 'Near Angkor Wat', 'ប្រាសាទបាគង': 'Near Angkor Wat', 'សៀមរាប': 'Near Angkor Wat', 'សូទ្រនិគម': 'Near Angkor Wat', 'ស្រីស្នំ': 'Near Angkor Wat', 'ស្វាយលើ': 'Near Angkor Wat', 'វ៉ារិន': 'Near Angkor Wat'}
            # Use the get() method to get the value from the dictionary
            return translate.get(match.group(0), match.group(0).title())





    return None

# Loop through all elements and extract the location
locations = []
for description in df['Post Description']:
    location = extract_location(description)
    locations.append(location)

# Print the extracted locations
for location in locations:
    print(location)




Toul Kork
Sen Sok
None
Chamkar Mon
None
Chroy Changvar
Chroy Changvar
Mean Chey
Mean Chey
Sen Sok
Toul Kork
Toul Kork
Toul Kork
None
None
Chroy Changvar
Kampong Som
None
Sen Sok
None
Toul Kork
None
None
None
None
None
None
Prampir Makara
None
Sen Sok
Chamkar Mon
Toul Kork
Toul Kork
Boeng Keng Kang
Toul Kork
Sen Sok
Sen Sok
Toul Kork
Sen Sok
Toul Kork
None
Toul Kork
Kampong Som
Toul Kork
None
None
None
Toul Kork
None
Toul Kork
None
None
None
None
None
Russey Keo
None
None
Chroy Changvar
Daun Penh
Daun Penh
Sen Sok
None
None
Sen Sok
Sen Sok
None
Sen Sok
None
Sen Sok
Toul Kork
Sen Sok
None
None
Sen Sok
None
None
Toul Kork
None
None
Pur Senchey
Toul Kork
Toul Kork
None
Sen Sok
None
Sen Sok
Sen Sok
Sen Sok
Chroy Changvar
None
Mean Chey
Sen Sok
Sen Sok
None
Sen Sok
Sen Sok
None
Sen Sok
None
None
None
None
None
None
None
Sen Sok
Chroy Changvar
None
None
None
Sen Sok
Sen Sok
None
None
None
None
None
None
None
Chamkar Mon
Toul Kork
Toul Kork
Sen Sok
Chamkar Mon
None
Sen Sok
Toul Kork
Boeng Keng

In [160]:
location_df = pd.DataFrame(locations)
location_df.value_counts()

Sen Sok            221
Toul Kork          110
Chroy Changvar      55
Chamkar Mon         40
Boeng Keng Kang     29
Daun Penh           28
Pur Senchey         28
Mean Chey           24
Near Angkor Wat     20
Prampir Makara      19
Kampong Som         17
Chbar Ampov         16
Russey Keo           7
Aeon                 2
dtype: int64

In [161]:
df['Sub Location'] = df['Post Description'].apply(extract_location)

In [162]:
import re

def extract_bedroom(description):
    if isinstance(description, str):
        match = re.search(r'បន្ទប់គេង\s*(\d+)', description)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bedroom', description)
        if match:
            return int(match.group(1))
        match = re.search(r'\+(\d+)\s*bedroom', description)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*Bedroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'-(\s*\d+)\s*bed\s*room', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'-(\s*\d+)\s*bedroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់គេង\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bedrooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bed\s*rooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'Bedroom:\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'Bedroom\s+(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់គេង៖\s*(\d+)', description)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bed\s*rooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*-?\s*bedroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់គេង\s*:\s*([១២៣៤៥៦៧៨៩១០]+)', description, re.IGNORECASE)
        if match:
            khmer_num = match.group(1)
            translate = {'១': 1, '២': 2, '៣': 3, '៤': 4, '៥': 5, '៦': 6, '៧': 7, '៨': 8, '៩': 9, '១០': 10}
            return translate.get(khmer_num, None)
        match = re.search(r'Bedrooms\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bedroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់គេង\s*[:：]\s*(\d+)[^\d\s]*|បន្ទប់គេង\s+(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        


    return None

# Loop through all elements and extract the bedroom information
bedrooms = []
for description in df['Post Description']:
    bedroom = extract_bedroom(description)
    bedrooms.append(bedroom)

# Print the extracted bedroom information
for bedroom in bedrooms:
    bedroom


In [163]:
bedrooms = pd.DataFrame(bedrooms)
bedrooms.value_counts().sum()

781

In [164]:
df['Bedrooms'] = df['Post Description'].apply(extract_bedroom)

In [165]:
import re

def extract_bathroom(description):
    if isinstance(description, str):
        match = re.search(r'បន្ទប់ទឹក\s*(\d+)', description)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*Bathroom', description)
        if match:
            return int(match.group(1))
        match = re.search(r'\+(\d+)\s*Bathroom', description)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*Bathroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'-(\s*\d+)\s*bath\s*room', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'-(\s*\d+)\s*bathroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់ទឹក\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bathrooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bathrooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bath\s*rooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'Bathroom:\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'Bathroom\s+(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់ទឹក៖\s*(\d+)', description)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bath\s*rooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*Bathrooms', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*-?\s*bathroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់ទឹក/\s*([១២៣៤៥៦៧៨៩១០]+)', description, re.IGNORECASE)
        if match:
            khmer_num = match.group(1)
            translate = {'១': 1, '២': 2, '៣': 3, '៤': 4, '៥': 5, '៦': 6, '៧': 7, '៨': 8, '៩': 9, '១០': 10}
            return translate.get(khmer_num, None)
        match = re.search(r'បន្ទប់ទឹក\s*:\s*([១២៣៤៥៦៧៨៩១០]+)', description, re.IGNORECASE)
        if match:
            khmer_num = match.group(1)
            translate = {'១': 1, '២': 2, '៣': 3, '៤': 4, '៥': 5, '៦': 6, '៧': 7, '៨': 8, '៩': 9, '១០': 10}
            return translate.get(khmer_num, None)
        match = re.search(r'Bathrooms\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s*bathroom', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'បន្ទប់ទឹក\s*[:：]\s*(\d+)[^\d\s]*|បន្ទប់ទឹក\s+(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))

        

    return None

# Loop through all elements and extract the bedroom information
bathrooms = []
for description in df['Post Description']:
    bathroom = extract_bathroom(description)
    bathrooms.append(bathroom)

# Print the extracted bedroom information
for bathroom in bathrooms:
    bathroom

In [166]:
bathrooms = pd.DataFrame(bathrooms)
bathrooms.value_counts().sum()

522

In [167]:
df['Bathrooms'] = df['Post Description'].apply(extract_bathroom)

In [168]:
import re

In [169]:
def extract_floor_number(description):
    if isinstance(description, str):
        # Search for floor number in English format (e.g., 7th floor)
        match = re.search(r'\b(\d+)(?:st|nd|rd|th)\s+floor\b', description, re.IGNORECASE)
        if match:
            return int(match.group(1))

        # Search for floor number in Khmer language format (e.g., ជាន់ទី៧)
        match = re.search(r'ជាន់ទី([១២៣៤៥៦៧៨៩០]+)', description)
        if match:
            khmer_numbers = {'១': 1, '២': 2, '៣': 3, '៤': 4, '៥': 5, '៦': 6, '៧': 7, '៨': 8, '៩': 9, '០': 0}
            khmer_number = match.group(1)
            floor_number = ''.join(str(khmer_numbers[digit]) for digit in khmer_number)
            return int(floor_number)

    return None

# Loop through all elements and extract the floor numbers
floor_numbers = []
for description in df['Post Description']:
    floor_number = extract_floor_number(description)
    floor_numbers.append(floor_number)

# Print the extracted floor numbers
for floor_number in floor_numbers:
    print(floor_number)

None
19
15
None
9
25
22
6
6
None
4
4
4
None
12
6
None
None
None
None
None
None
6
None
None
None
18
None
None
3
16
None
None
None
None
None
None
None
None
4
None
None
None
24
32
6
6
None
None
None
17
None
6
6
6
None
8
None
None
None
None
None
22
None
None
5
None
None
1
None
None
21
None
None
5
None
None
None
None
14
None
None
None
None
5
None
None
28
None
None
None
None
None
None
None
None
None
None
None
None
None
18
None
18
None
6
None
None
None
None
None
9
30
None
None
None
None
10
None
17
13
None
16
None
13
None
None
69
None
None
None
None
None
None
18
None
None
None
4
6
None
None
None
None
None
None
None
None
None
None
None
47
None
18
None
None
7
None
None
None
18
11
None
None
None
None
6
None
20
29
27
None
None
None
None
None
None
6
None
10
None
4
None
None
17
None
None
12
None
None
None
None
None
8
43
None
None
None
None
None
None
None
None
None
None
27
None
11
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
13
None
None
None
None
None
None
6
None
N

In [170]:
import re

def extract_floor_number(description):
    if isinstance(description, str):
        # Search for floor number in the format "Floor 6" and select the numeric value (6)
        match = re.search(r'Floor\s+(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))

        # Search for floor number in the format "6th floor" and select the numeric value (6)
        match = re.search(r'(\d+)(?:st|nd|rd|th)\s+floor', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        
        # Search for floor number in the format "Floor: 08" and select the numeric value (8)
        match = re.search(r'Floor:\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        # Search for floor number in the format "Floor: 11" and select the numeric value (11)
        match = re.search(r'Floor\s*[:：]\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        # Search for floor number in the format "ជាន់ទី ：11" and select the numeric value (11)
        match = re.search(r'ជាន់ទី\s*[:：]\s*(\d+)', description, re.UNICODE)
        if match:
            return int(match.group(1))
         # Search for floor number in the format "Floor : 13th" and select the numeric value (13)
        match = re.search(r'Floor\s*[:：]\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        # Search for floor number in the format "3rd Floor" and select the numeric value (3)
        match = re.search(r'(\d+)(?:st|nd|rd|th)\s+Floor', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        # Search for floor number in the format "ជាន់ទី 3" and select the numeric value (3)
        match = re.search(r'ជាន់ទី\s+(\d+)', description)
        if match:
            return int(match.group(1))
        match = re.search(r'floor\s+(\d+)(?:st|nd|rd|th)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        # Search for floor number in Khmer language format (e.g., ជាន់ទី៧)
        match = re.search(r'ជាន់ទី([១២៣៤៥៦៧៨៩០]+)', description)
        if match:
            khmer_numbers = {'១': 1, '២': 2, '៣': 3, '៤': 4, '៥': 5, '៦': 6, '៧': 7, '៨': 8, '៩': 9, '០': 0}
            khmer_number = match.group(1)
            floor_number = ''.join(str(khmer_numbers[digit]) for digit in khmer_number)
            return int(floor_number)
        match = re.search(r'Floor:\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'(\d+)\s+floors', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'ជាន់ទី\s*:\s*(\d+)', description)
        if match:
            return int(match.group(1))
        match = re.search(r'floor\s+(\d+)(?:st|nd|rd|th)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'ជាន់ទី\s*([១២៣៤៥៦៧៨៩១០]+)', description, re.IGNORECASE)
        if match:
            khmer_num = match.group(1)
            translate = {'១': 1, '២': 2, '៣': 3, '៤': 4, '៥': 5, '៦': 6, '៧': 7, '៨': 8, '៩': 9, '១០': 10}
            return translate.get(khmer_num, None)
        match = re.search(r'Floor\s*:\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'Floor\s*[:：]\s*(\d+)', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'Floor\s*[:：]\s*(\d+)[^\d\s]*', description, re.IGNORECASE)
        if match:
            return int(match.group(1))
        match = re.search(r'Floor:\s*(\d+)', description, re.IGNORECASE)
        
        if match:
            return int(match.group(1))

    return None

# Loop through all elements and extract the floor numbers
floor_numbers = []
for description in df['Post Description']:
    floor_number = extract_floor_number(description)
    
    if not floor_number:
          # Search two options above if not found
        match = re.search(r'ជាន់ទី\s+(\d+)', description)
        if match:
            floor_number = int(match.group(1)) - 2 if int(match.group(1)) >= 2 else None
       
        # Search two options above if not found
        match = re.search(r'(\d+)(?:st|nd|rd|th)\s+floor', description, re.IGNORECASE)
        if match:
            floor_number = int(match.group(1)) - 2 if int(match.group(1)) >= 2 else None
    floor_numbers.append(floor_number)

# Print the extracted floor numbers
for floor_number in floor_numbers:
    print(floor_number)


6
19
15
None
9
25
22
6
6
16
4
4
4
11
12
6
None
None
13
None
10
38
6
None
45
8
18
None
4
3
16
None
13
26
None
None
None
None
9
16
77
20
None
24
10
6
6
15
None
15
17
None
6
18
6
None
8
30
None
37
37
7
22
None
None
5
9
12
1
None
18
21
None
None
5
19
13
1
None
14
15
None
8
7
5
None
None
28
None
None
None
None
11
None
None
None
None
None
14
None
None
18
None
18
None
6
9
None
54
15
None
9
30
20
None
20
None
4
17
17
13
None
16
7
13
None
22
2
None
3
None
None
None
None
18
None
None
None
4
6
None
9
None
13
None
13
None
15
None
17
9
47
None
18
None
None
7
None
None
None
18
11
8
None
12
None
6
None
20
29
27
None
None
42
7
17
None
6
None
10
12
4
None
None
17
8
None
2
None
None
None
None
None
8
43
26
None
None
None
15
None
None
None
17
9
27
9
11
None
45
None
None
None
None
13
None
None
11
6
None
None
None
None
None
13
None
None
None
None
6
None
6
None
32
8
25
19
None
21
None
12
None
12
None
6
None
None
None
12
None
54
None
None
None
None
None
32
5
None
18
11
3
18
None
None
None
None
None
14
1
23
No

In [171]:
len(floor_numbers)

1547

In [172]:
df_floor = pd.DataFrame(floor_numbers)

df_floor.value_counts().sum()

683

In [173]:
# Create a new column 'Floor' in the dataframe and extract the floor numbers
df['Floor'] = df['Post Description'].apply(extract_floor_number)

In [174]:
df

Ad ID        Category   Locations     Posted   Size(m2)  Bedroom  \
0     8538993  Condo for Sale  Phnom Penh  06-Jul-23        34      NaN   
1     8517524  Condo for Sale  Phnom Penh  06-Jul-23        58      NaN   
2     9617339  Condo for Sale  Phnom Penh  03-Jul-23        34      NaN   
3     9617339  Condo for Sale  Phnom Penh  03-Jul-23        34      NaN   
4     8134344  Condo for Sale  Phnom Penh  09-Apr-23        57      NaN   
...       ...             ...         ...        ...       ...      ...   
1542  9669962  Condo for Sale  Phnom Penh  07-Jul-23        57      NaN   
1543  9670149  Condo for Sale  Phnom Penh  08-Jul-23    298616      NaN   
1544  9665839  Condo for Sale  Phnom Penh  07-Jul-23       119      NaN   
1545  8528328  Condo for Sale  Phnom Penh  07-Jul-23        32      NaN   
1546  8750427  Condo for Sale  Phnom Penh  07-Jul-23        32      NaN   

      Bathroom                                               Link  \
0          NaN  https://www.khmer24.com/en/property/new-condo-...   
1          NaN  https://www.khmer24.com/en/property/vista-cond...   
2          NaN  https://www.khmer24.com/en/property/condo-uk-5...   
3          NaN  https://www.khmer24.com/en/property/condo-%E1%...   
4          NaN  https://www.khmer24.com/en/property/condo-for-...   
...        ...                                                ...   
1542       NaN  https://www.khmer24.com/en/property/ud83cudfe0...   
1543       NaN  https://www.khmer24.com/en/property/condo-sale...   
1544       NaN  https://www.khmer24.com/en/property/beautifull...   
1545       NaN  https://www.khmer24.com/en/property/%E1%9E%81%...   
1546       NaN  https://www.khmer24.com/en/property/chip-mong-...   

                                                  Title     Price  \
0                                    New condo for sell   $58,000   
1                              Vista Condo Aeon2 Urgent   $75,000   
2                                Condo UK 548 for Sales   $42,000   
3     Condo សម្រាប់ជួល/Condo for Rent (The Peak Priv...      $800   
4                                   Condo for sale 57m2   $72,000   
...                                                 ...       ...   
1542  🏠ខុនដូ Agile Sky Residence (ជាន់ទី31) សម្រាប់ជ...      $900   
1543                     Condo sale 2Bedroom លក់បន្ទាន់   $17,900   
1544  --- BEAUTIFULL WHOLE CORNER Three Bedrooms at ...  $350,000   
1545  ខុនដូ 1 បន្ទប់គេង ត្រូវការលក់បន្ទាន់ Park Land...   $10,000   
1546                           Chip Mong Parkland Condo   $59,500   

                                       Post Description Sub Location  \
0     Very special promotion!! Full price $58,000 bu...    Toul Kork   
1     ខុនដូសម្រាប់លក់ VISTA Condo\n\r\n(English Belo...      Sen Sok   
2     បន្ទប់ខុនដូប្រភេទ Studio (UK Condo 548)\n\rកណ្...         None   
3     Property Code: VBRE00586\n\r\nCondo សម្រាប់ជួល...  Chamkar Mon   
4     Fully furnished condo for sale / rent \n\nOwne...         None   
...                                                 ...          ...   
1542  (English Below)\n\r\n🏠ខុនដូ Agile Sky Residenc...         None   
1543  ខុ​នដូទំនេីក្នុងគម្រោងMorgan Enmainson \n\nប្រ...         None   
1544  --- BEAUTIFULL WHOLE CORNER Three Bedrooms at ...      Sen Sok   
1545  អ្នកលក់ម្ចាស់ផ្ទាល់ និងអាចចូលស្នាក់នៅខែតុលានេះ...   Russey Keo   
1546  -Contingency Service Per Month：44.8$ including...         None   

      Bedrooms  Bathrooms  Floor  
0          1.0        1.0    6.0  
1          NaN        NaN   19.0  
2          NaN        NaN   15.0  
3          1.0        NaN    NaN  
4          1.0        1.0    9.0  
...        ...        ...    ...  
1542       1.0        1.0   31.0  
1543       2.0        NaN    NaN  
1544       3.0        2.0   24.0  
1545       1.0        1.0    NaN  
1546       NaN        NaN    NaN  

[1547 rows x 15 columns]

In [175]:
df.isnull().sum()

Ad ID                  0
Category               0
Locations              0
Posted                 0
Size(m2)               0
Bedroom             1547
Bathroom            1547
Link                   0
Title                  0
Price                  0
Post Description       0
Sub Location         931
Bedrooms             766
Bathrooms           1025
Floor                864
dtype: int64

In [176]:
df.to_csv('CondoData_Regex7920231237.csv', index= False)

----

In [49]:

    page = int(input("Number of pages :"))
    request_url = []
    for i in range(0,page*50,50):
        url = f"https://www.khmer24.com/en/search.html?q=condo&category=&per_page={i}"
        request_url=Request(url,headers={"User-Agent":"Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36"})
        get_open = urlopen(request_url).read()
        get_open_bs = bs(get_open)


Number of pages :2


In [50]:

list_item = get_open_bs.find_all('li', class_="item")

In [51]:
list_item

[<li class="item">
 <a class="border post" href="https://www.khmer24.com/en/property/ខនដ-pearla-palace-នសងកតទលសវយពរ-ជនទ-16-បនទបកង-adid-8729386.html" title="ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ជាន់ទី 16 បន្ទប់កែង">
 <article>
 <div class="item-image">
 <img alt="ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ជាន់ទី 16 បន្ទប់កែង" class="img-cover lazy" data-src="https://images.khmer24.co/22-12-21/s--pearla-palace-16--104992167157404697705289-b.jpg" src="https://www.khmer24.com//images/image-placeholder-256.png"/>
 </div>
 <div class="item-detail">
 <h2 class="item-title truncate truncate-2">ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ជាន់ទី 16 បន្ទប់កែង</h2>
 <p class="description truncate truncate-2">ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ខណ្ឌចំការមន ត្រូវការលក់បន្ទាន់
 * តម្លៃត្រឹមតែ៖ 150000$
 * ទំហំ៖ 81,</p> <ul class="list-unstyled summary">
 <li>Phnom Penh</li>
 <li><time datetime="2023-07-06">Yesterday</time></li>
 </ul>
 <p class="item-prices m-0 text-red"><span class="price">$1

In [4]:
    get_open = urlopen(request_url).read()
    get_open_bs = bs(get_open)
    get_open_bs

<!DOCTYPE html>
<html lang="en">
<head>
<meta content="Vj3nFdA-uZGZFOP3ZajI-jYDUUPyNZL-EMAE5WbY94A" name="google-site-verification"/>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="#028dcf" name="theme-color"/>
<meta content="width=device-width" name="viewport"/>
<link href="https://www.khmer24.com/favicon.ico" rel="shortcut icon"/>
<!-- <link href="https://fonts.googleapis.com/css?family=Hanuman" rel="stylesheet"> -->
<!--[if lt IE 9]>
		  <script src="https://oss.maxcdn.com/libs/html5shiv/3.7.0/html5shiv.js"></script>
		<![endif]-->
<title>Search "condo" in List all Ads in Cambodia - Khmer24.com</title>
<meta content="List all Ads, List all Ads in Cambodia, List all Ads in Cambodia, buy and sell, online shopping, shopping, shopping in Cambodia, real estate, classified, listing, post free ads, classified ads, property, home, land, car, mobile phone, computer, electronic, furniture, job, service, product price" name="keywords"/>
<meta cont

In [5]:
# get_open

In [6]:
list_item = get_open_bs.find_all('li',class_ = 'item')
list_item

[<li class="item">
 <a class="border post" href="https://www.khmer24.com/en/property/condo-for-sale-unit-អចចលនបន-adid-9330721.html" title="Condo For sale (unit អាចចូលនៅបាន)">
 <article>
 <div class="item-image">
 <img alt="Condo For sale (unit អាចចូលនៅបាន)" class="img-cover lazy" data-src="https://images.khmer24.co/23-04-24/s-condo-for-sale-250184168230345390462852-b.jpg" src="https://www.khmer24.com//images/image-placeholder-256.png"/>
 </div>
 <div class="item-detail">
 <h2 class="item-title truncate truncate-2">Condo For sale (unit អាចចូលនៅបាន)</h2>
 <p class="description truncate truncate-2">Chip Mong TK ម្ចាស់ដើមលក់
 កំពុងឋិតក្នុងការបង់30%ឥតការប្រាក់3ឆ្នាំ លក់វិញយកតែ$15,000 ងាយស្រួល បង់តក៍បាន ផ្ដាច់ក</p> <ul class="list-unstyled summary">
 <li>Phnom Penh</li>
 <li><time datetime="2023-07-06">23 hours ago</time></li>
 </ul>
 <p class="item-prices m-0 text-red"><span class="price">$15,000</span></p>
 </div>
 </article>
 </a>
 </li>,
 <li class="item">
 <a class="border post" href="h

In [7]:
list_item[0].a.get('href')

'https://www.khmer24.com/en/property/condo-for-sale-unit-អចចលនបន-adid-9330721.html'

In [58]:
links = []
for i in range(len(list_item)):
    a_tag = list_item[i].a # get the <a> tag
    if a_tag: # check if it exists
        url_link = quote(a_tag.get('href'),safe='/:') # get the href attribute
        links.append(url_link) # append to the list

In [59]:
len(links)

50

In [60]:
from urllib.request import urlopen
import urllib.parse
html_link = []
link_condo_sale = []
for j, link in enumerate(links):
    request_link = Request(link,headers={"User-Agent":"Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36"})
    get_link = urlopen( request_link).read()
    item_short_description =bs(get_link).find('div', class_="item-short-description p-3 position-relative")
        # Find the span element with the class "title" and extract the category value
    category_element = item_short_description.find('span', class_='title', text='Category :')
    category = category_element.find_next_sibling('span').text.strip()
    try:
        if category == 'Condo for Sale':
            print(f"{j} : {link} ")
            link_condo_sale.append(links2)
        else:
            continue # or omit this line
    except:
            # handle any exception here
        pass
    html_link.append(bs(get_link))

0 : https://www.khmer24.com/en/property/%E1%9E%81%E1%9E%93%E1%9E%8A-pearla-palace-%E1%9E%93%E1%9E%9F%E1%9E%84%E1%9E%80%E1%9E%8F%E1%9E%91%E1%9E%9B%E1%9E%9F%E1%9E%9C%E1%9E%99%E1%9E%96%E1%9E%9A-%E1%9E%87%E1%9E%93%E1%9E%91-16-%E1%9E%94%E1%9E%93%E1%9E%91%E1%9E%94%E1%9E%80%E1%9E%84-adid-8729386.html 
1 : https://www.khmer24.com/en/property/unit-condo-for-sale-now-adid-8829137.html 
2 : https://www.khmer24.com/en/property/the-garden-residency-condo-%E1%9E%8A%E1%9E%8E%E1%9E%84%E1%9E%9B%E1%9E%80%E1%9E%81%E1%9E%93%E1%9E%8A%E1%9E%9A%E1%9E%94%E1%9E%93%E1%9E%91%E1%9E%93-%E1%9E%8F%E1%9E%9B-%E1%9E%80%E1%9E%9A%E1%9E%98%E1%9E%91%E1%9E%95%E1%9E%9F%E1%9E%9A-%E1%9E%97%E1%9E%93%E1%9E%96%E1%9E%89-adid-8837997.html 
3 : https://www.khmer24.com/en/property/penthouse-2-bedrooms-for-sale-in-bkk-1-adid-8908815.html 
7 : https://www.khmer24.com/en/property/uk-condo-313-for-rent-or-sale-adid-8958365.html 
8 : https://www.khmer24.com/en/property/brand-new-condo-2br-99k-negotiable-adid-9008430.html 
9 : https://www.

In [61]:
type(html_link)

list

In [62]:
len(html_link)

27

In [63]:

for i, html in enumerate(html_link):    
    item_details = html.find('div', class_ = 'item-detail p-3')
    item_short_description =html.find('div', class_="item-short-description p-3 position-relative")
    # Find the span element with the class "title" and extract the category value
    category_element = item_short_description.find('span', class_='title', text='Category :')
    category = category_element.find_next_sibling('span').text.strip()
    print(category)

Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale
Condo for Sale


In [65]:
link_condo_sale = []
for i, links2 in enumerate(html_link):
    item_short_description =links2.find('div', class_="item-short-description p-3 position-relative")
    # Find the span element with the class "title" and extract the category value
    category_element = item_short_description.find('span', class_='title', text='Category :')
    category = category_element.find_next_sibling('span').text.strip()
    try:
        if category == 'Condo for Sale':
            print(f"{i} : {links2} ")
            link_condo_sale.append(links2)
        else:
            continue # or omit this line
    except:
        # handle any exception here
        pass

0 : <!DOCTYPE html>
<html lang="en">
<head prefix="og: http://ogp.me/ns# 
		fb: http://ogp.me/ns/fb# 
		product: http://ogp.me/ns/product#">
<meta content="Vj3nFdA-uZGZFOP3ZajI-jYDUUPyNZL-EMAE5WbY94A" name="google-site-verification"/>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="#028dcf" name="theme-color"/>
<meta content="width=device-width" name="viewport"/>
<link href="https://www.khmer24.com/favicon.ico" rel="shortcut icon"/>
<!-- <link href="https://fonts.googleapis.com/css?family=Hanuman" rel="stylesheet"> -->
<!--[if lt IE 9]>
		  <script src="https://oss.maxcdn.com/libs/html5shiv/3.7.0/html5shiv.js"></script>
		<![endif]-->
<title>ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ជាន់ទី 16 បន្ទប់កែង Price $150000.00 in Tuol Svay Prey Muoy, Boeng Keng Kang, Phnom Penh, Cambodia - Seiha Van ^^ | Khmer24.com</title>
<meta content="Condo for Sale Price $150000.00 in Tuol Svay Prey Muoy, Condo for Sale Price $150000.00 in Boeng Keng Kang, Con

9 : <!DOCTYPE html>
<html lang="en">
<head prefix="og: http://ogp.me/ns# 
		fb: http://ogp.me/ns/fb# 
		product: http://ogp.me/ns/product#">
<meta content="Vj3nFdA-uZGZFOP3ZajI-jYDUUPyNZL-EMAE5WbY94A" name="google-site-verification"/>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="#028dcf" name="theme-color"/>
<meta content="width=device-width" name="viewport"/>
<link href="https://www.khmer24.com/favicon.ico" rel="shortcut icon"/>
<!-- <link href="https://fonts.googleapis.com/css?family=Hanuman" rel="stylesheet"> -->
<!--[if lt IE 9]>
		  <script src="https://oss.maxcdn.com/libs/html5shiv/3.7.0/html5shiv.js"></script>
		<![endif]-->
<title>UK Condo 618 លក់បន្ទាន់​ Price $42000.00 in Boeng Kak Pir, Tuol Kouk, Phnom Penh, Cambodia - Mr Rith | Khmer24.com</title>
<meta content="Condo for Sale Price $42000.00 in Boeng Kak Pir, Condo for Sale Price $42000.00 in Tuol Kouk, Condo for Sale Price $42000.00 in Phnom Penh, Condo for Sale Size(m&lt;s

16 : <!DOCTYPE html>
<html lang="en">
<head prefix="og: http://ogp.me/ns# 
		fb: http://ogp.me/ns/fb# 
		product: http://ogp.me/ns/product#">
<meta content="Vj3nFdA-uZGZFOP3ZajI-jYDUUPyNZL-EMAE5WbY94A" name="google-site-verification"/>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="#028dcf" name="theme-color"/>
<meta content="width=device-width" name="viewport"/>
<link href="https://www.khmer24.com/favicon.ico" rel="shortcut icon"/>
<!-- <link href="https://fonts.googleapis.com/css?family=Hanuman" rel="stylesheet"> -->
<!--[if lt IE 9]>
		  <script src="https://oss.maxcdn.com/libs/html5shiv/3.7.0/html5shiv.js"></script>
		<![endif]-->
<title>Stop worrying when the rainy season comes at L'attrait BOEUNG KENG KANG Price $2000.00 in Boeng Keng Kang Muoy, Boeng Keng Kang, Phnom Penh, Cambodia - Ms Sok Vouchheng | Khmer24.com</title>
<meta content="Condo for Sale Price $2000.00 in Boeng Keng Kang Muoy, Condo for Sale Price $2000.00 in Boeng Ken

24 : <!DOCTYPE html>
<html lang="en">
<head prefix="og: http://ogp.me/ns# 
		fb: http://ogp.me/ns/fb# 
		product: http://ogp.me/ns/product#">
<meta content="Vj3nFdA-uZGZFOP3ZajI-jYDUUPyNZL-EMAE5WbY94A" name="google-site-verification"/>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="#028dcf" name="theme-color"/>
<meta content="width=device-width" name="viewport"/>
<link href="https://www.khmer24.com/favicon.ico" rel="shortcut icon"/>
<!-- <link href="https://fonts.googleapis.com/css?family=Hanuman" rel="stylesheet"> -->
<!--[if lt IE 9]>
		  <script src="https://oss.maxcdn.com/libs/html5shiv/3.7.0/html5shiv.js"></script>
		<![endif]-->
<title>Multi-purpose condo units at L'attrait BOEUNG KENG KANG Condo! Price $2000.00 in Boeng Keng Kang Muoy, Boeng Keng Kang, Phnom Penh, Cambodia - Ms Sok Vouchheng | Khmer24.com</title>
<meta content="Condo for Sale Price $2000.00 in Boeng Keng Kang Muoy, Condo for Sale Price $2000.00 in Boeng Keng Kang, C

In [24]:
len(link_condo_sale)

33

In [232]:
item_short_description =link_condo_sale[0].find('div', class_="item-short-description p-3 position-relative")
item_short_description

<div class="item-short-description p-3 position-relative">
<h1>ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ជាន់ទី 16 បន្ទប់កែង</h1>
<div>
<p class="price price_tag"><b class="price">$150,000</b></p>
</div>
<ul class="list-unstyled item-info m-0">
<li>
<span class="title">Ad ID :</span>
<span class="value">8729386</span>
</li>
<li>
<span class="title">Category :</span>
<span class="value">Condo for Sale</span>
</li>
<li>
<span class="title">Locations :</span>
<span class="value">Phnom Penh</span>
</li>
<li>
<span class="title">Posted :</span>
<span class="value"><time datetime="2023-07-06 07:28:40">06-Jul-23</time></span>
</li>
</ul>
<a class="btn-save-item save_ad" href="https://www.khmer24.com/en/save-ad/8729386.html" rel="nofollow" title="Save">
<i class="icon icon-bookmark text_gray"></i>
</a>
<a class="btn-share-item share_ad" href="https://www.facebook.com/sharer/sharer.php?u=https://www.khmer24.com/en/property/ខនដ-pearla-palace-នសងកតទលសវយពរ-ជនទ-16-បនទបកង-adid-8729386.html" onclick=

In [100]:
# Scrape the price
price_element = item_short_description.select_one('.price.price_tag b')
price = price_element.text.strip() if price_element else None
print('Price:', price)

# Scrape the information list
information_list = []
info_elements = item_short_description.select('.item-info li')
for info_element in info_elements:
    title = info_element.select_one('.title').text.strip()
    value = info_element.select_one('.value').text.strip()
    information_list.append((title, value))
    
print('Information:')
for title, value in information_list:
    print(title, ':', value)

Price: $150,000
Information:
Ad ID : : 8729386
Category : : Condo for Sale
Locations : : Phnom Penh
Posted : : 06-Jul-23


In [121]:
item_details = link_condo_sale[0].find('div', class_ = 'item-detail p-3')
item_details

<div class="item-detail p-3">
<h2>Description</h2>
<ul class="list-unstyled item-fields">
<li><div><span class="title">Size(m<sup>2</sup>):</span><span class="value">82</span></div></li> </ul>
<p class="post-description">ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ខណ្ឌចំការមន ត្រូវការលក់បន្ទាន់<br/>
* តម្លៃត្រឹមតែ៖ 150000$<br/>
* ទំហំ៖ 81,85 ម៉ែត្រការ៉េ<br/>
* បន្ទប់ធំទូលាយ<br/>
* ខុនដូរមាន៖ បន្ទប់គេង 2 និងបន្ទប់ទឹក 2 ​<br/>
* បែរមុខទៅខាងត្បូង<br/>
* នៅជាន់ទី 16<br/>
* លក្ខណៈពិសេស៖ មានកន្លែងចតឡាន <br/>
* សម្ភារៈ៖ មាន ម៉ាសុីនត្រជាក់ 3 <br/>
* មានអាងហែលទឹក កន្លែងហាត់ប្រាណ ណឹងកន្លែងអង្គុយស្រប យកខ្យល់អាកាស.<br/>
* អ្វីដែរពិសេសខុសដូរនៅកែងអាចមេីលទេសភាពបាន3ទិស<br/>
* មានភាពងាយស្រួលក្នុងការរស់នៅមានលក្ខណ:ទាន់សម័យ​ មានសុវត្តិភាព និង ផាសុខភាព។<br/>
<br/>
ទំនាក់ទំនង<br/>
Phone <a class="btn_show_phone btn_phone smart" data-value="0968818882" href="tel:0968818882">0968818xxx <i>ចុចដើម្បីតេ/Click To Call</i></a><br/>
Telegram <a class="btn_show_phone btn_phone smart" data-value="0968818882" href="tel:

In [165]:
 item_short_description2 = link_condo_sale[0].find('ul', class_="list-unstyled item-fields")
item_short_description2

<ul class="list-unstyled item-fields">
<li><div><span class="title">Size(m<sup>2</sup>):</span><span class="value">82</span></div></li> </ul>

In [245]:
# Scrape the size
size_element = item_details.select_one('.item-fields .value')
size = size_element.text.strip() if size_element else None
print('Size:', size)

# Scrape the entire text in the post description
post_description_element = item_details.select_one('.post-description')
post_description = post_description_element.get_text(separator='\n').strip() if post_description_element else None
print('Post Description:')
post_description

Size: 82
Post Description:


'ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ខណ្ឌចំការមន ត្រូវការលក់បន្ទាន់\n\r\n* តម្លៃត្រឹមតែ៖ 150000$\n\r\n* ទំហំ៖ 81,85 ម៉ែត្រការ៉េ\n\r\n* បន្ទប់ធំទូលាយ\n\r\n* ខុនដូរមាន៖ បន្ទប់គេង 2 និងបន្ទប់ទឹក 2 \u200b\n\r\n* បែរមុខទៅខាងត្បូង\n\r\n* នៅជាន់ទី 16\n\r\n* លក្ខណៈពិសេស៖ មានកន្លែងចតឡាន \n\r\n* សម្ភារៈ៖ មាន ម៉ាសុីនត្រជាក់ 3 \n\r\n* មានអាងហែលទឹក កន្លែងហាត់ប្រាណ ណឹងកន្លែងអង្គុយស្រប យកខ្យល់អាកាស.\n\r\n* អ្វីដែរពិសេសខុសដូរនៅកែងអាចមេីលទេសភាពបាន3ទិស\n\r\n* មានភាពងាយស្រួលក្នុងការរស់នៅមានលក្ខណ:ទាន់សម័យ\u200b មានសុវត្តិភាព និង ផាសុខភាព។\n\n\n\r\nទំនាក់ទំនង\n\r\nPhone \n0968818xxx \nចុចដើម្បីតេ/Click To Call\n\r\nTelegram \n0968818xxx \nចុចដើម្បីតេ/Click To Call\n\n\n\r\nHere:\n\n\n\r\n* The condo is located in a very convenient area which consist of markets, hospitals, clinics, schools etc.\n\r\n* 10mn walk to the Olympic Market, 15mn walk to the Chinese Embassy, 30mn walk to the Olympic Stadium\n\r\n* Less than 1 hour drive to the Phnom Penh International Airport\n\r\n* The condo is on the 16th f

In [117]:
html_codes = []
for i, html in enumerate(link_condo_sale):    
    item_details = html.find('div', class_ = 'item-detail p-3')
    print(item_details)
    html_codes.append(item_details)

<div class="item-detail p-3">
<h2>Description</h2>
<ul class="list-unstyled item-fields">
<li><div><span class="title">Size(m<sup>2</sup>):</span><span class="value">82</span></div></li> </ul>
<p class="post-description">ខុនដូ Pearla Palace នៅសង្កាត់ទួលស្វាយព្រៃ ខណ្ឌចំការមន ត្រូវការលក់បន្ទាន់<br/>
* តម្លៃត្រឹមតែ៖ 150000$<br/>
* ទំហំ៖ 81,85 ម៉ែត្រការ៉េ<br/>
* បន្ទប់ធំទូលាយ<br/>
* ខុនដូរមាន៖ បន្ទប់គេង 2 និងបន្ទប់ទឹក 2 ​<br/>
* បែរមុខទៅខាងត្បូង<br/>
* នៅជាន់ទី 16<br/>
* លក្ខណៈពិសេស៖ មានកន្លែងចតឡាន <br/>
* សម្ភារៈ៖ មាន ម៉ាសុីនត្រជាក់ 3 <br/>
* មានអាងហែលទឹក កន្លែងហាត់ប្រាណ ណឹងកន្លែងអង្គុយស្រប យកខ្យល់អាកាស.<br/>
* អ្វីដែរពិសេសខុសដូរនៅកែងអាចមេីលទេសភាពបាន3ទិស<br/>
* មានភាពងាយស្រួលក្នុងការរស់នៅមានលក្ខណ:ទាន់សម័យ​ មានសុវត្តិភាព និង ផាសុខភាព។<br/>
<br/>
ទំនាក់ទំនង<br/>
Phone <a class="btn_show_phone btn_phone smart" data-value="0968818882" href="tel:0968818882">0968818xxx <i>ចុចដើម្បីតេ/Click To Call</i></a><br/>
Telegram <a class="btn_show_phone btn_phone smart" data-value="0968818882" href="tel:

In [233]:
html_code

<div class="item-detail p-3">
<h2>Description</h2>
<ul class="list-unstyled item-fields">
<li><div><span class="title">Size(m<sup>2</sup>):</span><span class="value">48</span></div></li> </ul>
<p class="post-description">🙏សូមស្វាគមន៍មកOrient Ritz Condo<br/>
🏢 ខុនដូសម្រាប់លក់ ! 🏘 (គម្រោង Orient Ritz Condo ទួលគោក) នៅចំកណ្តាលទីក្រុង<br/>
✨ទីតាំងល្អខ្លាំង មនុស្សអ៊ូរអរ មានហាងបាយ ហាងកាហ្វេ ផ្សារ ផ្សារទំនើប ម៉ាត ធនាគារ មន្ទីរពេទ្យ និងកន្លែងដើរលេងជាច្រើននៅជិតខុនដូរ<br/>
👉Orient Ritz condo មាន:18ជាន់<br/>
🅿️ជាន់ក្រោមដី នឹង ជាន់ទី1គឺចំណតឡាន<br/>
🌟ជាន់ទី18គឺមានអាងហែលទឹកលើអាកាស បន្ទប់ហាត់ប្រាណ នឹងមានSkybar<br/>
<br/>
🏠បន្ទប់លក់ស្ថិតនៅជាន់ទី14 <br/>
ជាប្រភេទ បន្ទប់Studio មានទំហំ 48m2<br/>
🏷សំរាប់តម្លៃ $68000-ចរចាបាន<br/>
👉ទិញភ្លាម ចូលនៅបានភ្លាម រឺ បងអាចដាក់ជួលបាន ធានាមានភ្ញៀវជួលភ្លាមៗ រយះពេលជួលអាចរហូតដល់ 2ឆ្នាំ <br/>
👉តំលៃ3XX$ ក្នុងមួយខែ (សំរាប់ការជួលត្រលប់មកវិញ)<br/>
<br/>
🎁ប្រគល់សម្ភារៈប្រើប្រាស់មានទាំងអស់ ក្នុងបន្ទប់ដូចជា៖ <br/>
🔹ទូរទស្សន៍ <br/>
🔹ទូទឹកកក <br/>
🔹ម៉ាស៊ីនបោកខោអាវ <br/>
🔹ម៉ាស៊ីនប៊ឺត

In [119]:
# Find all <p> elements with the class "post-description"
description_elements = html_code.find_all('p', class_='post-description')
description_elements

[<p class="post-description">🙏សូមស្វាគមន៍មកOrient Ritz Condo<br/>
 🏢 ខុនដូសម្រាប់លក់ ! 🏘 (គម្រោង Orient Ritz Condo ទួលគោក) នៅចំកណ្តាលទីក្រុង<br/>
 ✨ទីតាំងល្អខ្លាំង មនុស្សអ៊ូរអរ មានហាងបាយ ហាងកាហ្វេ ផ្សារ ផ្សារទំនើប ម៉ាត ធនាគារ មន្ទីរពេទ្យ និងកន្លែងដើរលេងជាច្រើននៅជិតខុនដូរ<br/>
 👉Orient Ritz condo មាន:18ជាន់<br/>
 🅿️ជាន់ក្រោមដី នឹង ជាន់ទី1គឺចំណតឡាន<br/>
 🌟ជាន់ទី18គឺមានអាងហែលទឹកលើអាកាស បន្ទប់ហាត់ប្រាណ នឹងមានSkybar<br/>
 <br/>
 🏠បន្ទប់លក់ស្ថិតនៅជាន់ទី14 <br/>
 ជាប្រភេទ បន្ទប់Studio មានទំហំ 48m2<br/>
 🏷សំរាប់តម្លៃ $68000-ចរចាបាន<br/>
 👉ទិញភ្លាម ចូលនៅបានភ្លាម រឺ បងអាចដាក់ជួលបាន ធានាមានភ្ញៀវជួលភ្លាមៗ រយះពេលជួលអាចរហូតដល់ 2ឆ្នាំ <br/>
 👉តំលៃ3XX$ ក្នុងមួយខែ (សំរាប់ការជួលត្រលប់មកវិញ)<br/>
 <br/>
 🎁ប្រគល់សម្ភារៈប្រើប្រាស់មានទាំងអស់ ក្នុងបន្ទប់ដូចជា៖ <br/>
 🔹ទូរទស្សន៍ <br/>
 🔹ទូទឹកកក <br/>
 🔹ម៉ាស៊ីនបោកខោអាវ <br/>
 🔹ម៉ាស៊ីនប៊ឺតផ្សែង - ចង្រ្កានគី្គសនី <br/>
 🔹ម៉ាស៊ីនត្រជាក់<br/>
 🔹គ្រែ - ពូក <br/>
 🔹ទូខោអាវ<br/>
 🔹សាឡុង - តុ<br/>
 <br/>
 👉ទឹក   0.68$/ 1m3<br/>
 👉ភ្លើង 0.25$/ 1kwh<br/>
 👉Parking 60$/ 

In [120]:


# Extract the text content from each element
descriptions = [element.get_text().strip() for element in description_elements]

# Print the scraped descriptions
for description in descriptions:
    print(description)

🙏សូមស្វាគមន៍មកOrient Ritz Condo
🏢 ខុនដូសម្រាប់លក់ ! 🏘 (គម្រោង Orient Ritz Condo ទួលគោក) នៅចំកណ្តាលទីក្រុង
✨ទីតាំងល្អខ្លាំង មនុស្សអ៊ូរអរ មានហាងបាយ ហាងកាហ្វេ ផ្សារ ផ្សារទំនើប ម៉ាត ធនាគារ មន្ទីរពេទ្យ និងកន្លែងដើរលេងជាច្រើននៅជិតខុនដូរ
👉Orient Ritz condo មាន:18ជាន់
🅿️ជាន់ក្រោមដី នឹង ជាន់ទី1គឺចំណតឡាន
🌟ជាន់ទី18គឺមានអាងហែលទឹកលើអាកាស បន្ទប់ហាត់ប្រាណ នឹងមានSkybar

🏠បន្ទប់លក់ស្ថិតនៅជាន់ទី14 
ជាប្រភេទ បន្ទប់Studio មានទំហំ 48m2
🏷សំរាប់តម្លៃ $68000-ចរចាបាន
👉ទិញភ្លាម ចូលនៅបានភ្លាម រឺ បងអាចដាក់ជួលបាន ធានាមានភ្ញៀវជួលភ្លាមៗ រយះពេលជួលអាចរហូតដល់ 2ឆ្នាំ 
👉តំលៃ3XX$ ក្នុងមួយខែ (សំរាប់ការជួលត្រលប់មកវិញ)

🎁ប្រគល់សម្ភារៈប្រើប្រាស់មានទាំងអស់ ក្នុងបន្ទប់ដូចជា៖ 
🔹ទូរទស្សន៍ 
🔹ទូទឹកកក 
🔹ម៉ាស៊ីនបោកខោអាវ 
🔹ម៉ាស៊ីនប៊ឺតផ្សែង - ចង្រ្កានគី្គសនី 
🔹ម៉ាស៊ីនត្រជាក់
🔹គ្រែ - ពូក 
🔹ទូខោអាវ
🔹សាឡុង - តុ

👉ទឹក   0.68$/ 1m3
👉ភ្លើង 0.25$/ 1kwh
👉Parking 60$/ 1ខែ 

✨មានសន្តិសុខ 24ម៉ោង សុវត្ថិភាពខ្ពស់ 

📍ទីតាំងស្ថិតនៅផ្លូវ150  ភូមិ3 សង្កាត់ទឹកល្អក់ទី 2 ខណ្ឌទួលគោក រាជធានីភ្នំពេញ ក្រោយវិទ្យាល័យសន្ធរមុខ3ផ្លូវ (ជិតផ្សារគីឡូលេខ4 )
🔎Location:

In [71]:
import re
#soup = bs(html_code, 'html.parser')
# Extract the floor
floor_match = re.search(r'- Floor: (\d+)(?:\w+)', html_code)
if floor_match:
    floor = floor_match.group(1)
else:
    floor = "Not found"

# Extract the location
location_match = re.search(r'- Location in (\w+(?:\s+\w+)*)', html_code)
if location_match:
    location = location_match.group(1)
else:
    location = "Not found"
print("Floor:", floor)
print("Location:", location)


TypeError: expected string or bytes-like object